# EDA

Let's have a first look at the data. 

The Variables in the files are:
* S1: heat power
* S2: flow rate
* S3: leader temperature (initial temperature)
* S4: return temperature

For the years 2020 and 2021 we also have the outside temperature at the location of the heat plant. 

We also have: 
* holydays in Bavaria (a lot!)
* school vacations in Bavaria

We will first focus only on the years 2020 and 2021, since here, we have all the data. For 2022, temperature is missing. 

## Read the data

In [1]:
import pandas as pd
#import seaborn as sns
import plotly.graph_objs as go
import plotly.express as px

In [2]:
df_2020 = pd.read_csv("../raw_data/2020_heat.csv", delimiter=";", index_col=False)
df_2021 = pd.read_csv("../raw_data/2021_heat.csv", delimiter=";", index_col=False)

df = pd.concat([df_2020, df_2021], ignore_index=True)
df.rename({"S1": "heat_power", "S2": "flow_rate", "S3": "leader_temp", "S4": "return_temp"}, axis=1, inplace=True)
df

Timestamp  heat_power  flow_rate  leader_temp  \
0      2020-01-01T00:15:00.000000+01:00     713.000  17650.000       81.000   
1      2020-01-01T00:30:00.000000+01:00     330.000   9600.000       81.000   
2      2020-01-01T00:45:00.000000+01:00     705.000  16730.000       81.000   
3      2020-01-01T01:00:00.000000+01:00     663.000  16890.000       81.000   
4      2020-01-01T01:15:00.000000+01:00     412.000  10690.000       81.000   
...                                 ...         ...        ...          ...   
69979  2021-12-30T23:00:00.000000+01:00     385.571  17884.286       81.857   
69980  2021-12-30T23:15:00.000000+01:00     436.500  20311.250       81.875   
69981  2021-12-30T23:30:00.000000+01:00     320.143  16380.000       81.714   
69982  2021-12-30T23:45:00.000000+01:00     302.250  17442.500       82.000   
69983  2021-12-31T00:00:00.000000+01:00     286.000  15648.571       81.857   

       return_temp  
0           46.000  
1           51.000  
2           44.000  
3           47.000  
4           48.000  
...            ...  
69979       62.857  
69980       62.750  
69981       64.714  
69982       66.625  
69983       65.857  

[69984 rows x 5 columns]

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 69984 entries, 0 to 69983
Data columns (total 5 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   Timestamp    69984 non-null  object 
 1   heat_power   69022 non-null  float64
 2   flow_rate    69022 non-null  float64
 3   leader_temp  69022 non-null  float64
 4   return_temp  69022 non-null  float64
dtypes: float64(4), object(1)
memory usage: 2.7+ MB


In [4]:
fig = px.line(data_frame=df, x="Timestamp", y="heat_power")
fig.show()

As we can see, there are some mssing values in october of 2020. There are also some values of zero, and in summer of 2021 one extremely learge peak. I don't know what to make of these right now, I will ignore them for now. 

## Fun with datetime
Everyones favorite pasttime: dealing with the datetime. Basically, I want the naive but local dattime as a variable. For now, I am not going to use datetime as the index, because of thing like daylight savings time. 


In [5]:
df.Timestamp = pd.to_datetime(df.Timestamp, infer_datetime_format=True, utc=True)


In [12]:
df.Timestamp = df.Timestamp.dt.tz_convert(tz="Europe/Berlin")

In [14]:
df.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 69984 entries, 0 to 69983
Data columns (total 8 columns):
 #   Column       Non-Null Count  Dtype                        
---  ------       --------------  -----                        
 0   Timestamp    69984 non-null  datetime64[ns, Europe/Berlin]
 1   heat_power   69022 non-null  float64                      
 2   flow_rate    69022 non-null  float64                      
 3   leader_temp  69022 non-null  float64                      
 4   return_temp  69022 non-null  float64                      
 5   time         69984 non-null  object                       
 6   week_nr      69984 non-null  UInt32                       
 7   weekday      69984 non-null  int64                        
dtypes: UInt32(1), datetime64[ns, Europe/Berlin](1), float64(4), int64(1), object(1)
memory usage: 4.1+ MB


In [15]:
df.head()

Timestamp  heat_power  flow_rate  leader_temp  return_temp  \
0 2020-01-01 00:15:00+01:00       713.0    17650.0         81.0         46.0   
1 2020-01-01 00:30:00+01:00       330.0     9600.0         81.0         51.0   
2 2020-01-01 00:45:00+01:00       705.0    16730.0         81.0         44.0   
3 2020-01-01 01:00:00+01:00       663.0    16890.0         81.0         47.0   
4 2020-01-01 01:15:00+01:00       412.0    10690.0         81.0         48.0   

       time  week_nr  weekday  
0  23:15:00        1        1  
1  23:30:00        1        1  
2  23:45:00        1        1  
3  00:00:00        1        2  
4  00:15:00        1        2

### Check for correlations
My guess would be that heat power is proportional to temperature difference times flow rate.

In [ ]:
df["heat_flow_calc"] = (df.leader_temp - df.return_temp) * df.flow_rate
df.head()

In [ ]:
df.columns

In [ ]:
fig = px.scatter_matrix(df.drop("Timestamp", axis=1))
fig.show()

In [ ]:
fig = px.scatter(data_frame=df, x="heat_power", y="heat_flow_calc")
fig.show()

That is indeed the case. So for now, we will drop all columns except the heat power. 

In [ ]:
df.drop(["flow_rate", "leader_temp", "return_temp", "heat_flow_calc"], axis=1, inplace=True)
df.head()

## Feature engineering
let's play with the datetime a bit.

In [18]:
#df["date"] = df.Timestamp.dt.date
df["time"] = df.Timestamp.dt.time
df["hour"] = df.Timestamp.dt.hour
df["week_nr"] = df.Timestamp.dt.isocalendar().week
df["weekday"] = df.Timestamp.dt.weekday

In [19]:
df.head()

Timestamp  heat_power  flow_rate  leader_temp  return_temp  \
0 2020-01-01 00:15:00+01:00       713.0    17650.0         81.0         46.0   
1 2020-01-01 00:30:00+01:00       330.0     9600.0         81.0         51.0   
2 2020-01-01 00:45:00+01:00       705.0    16730.0         81.0         44.0   
3 2020-01-01 01:00:00+01:00       663.0    16890.0         81.0         47.0   
4 2020-01-01 01:15:00+01:00       412.0    10690.0         81.0         48.0   

       time  week_nr  weekday  hour  
0  00:15:00        1        2     0  
1  00:30:00        1        2     0  
2  00:45:00        1        2     0  
3  01:00:00        1        2     1  
4  01:15:00        1        2     1